In [1]:
# imports
import pandas as pd
import numpy as np

from great_schools import get_nearby_schools, get_demographics
from distance import get_distance
from secret import get_key
from district_score import get_overall_rating

## Shaun and Daniela's Boston Public School Analysis
#### 2021.04.10

Fetch the API key from the local filesystem.

In [2]:
# get the API key
api_key_file = '../keys/api.key'
api_key = get_key(api_key_file)

Use the `nearby_schools` API endpoint to grab raw data of all schools within the maximum radius

In [3]:
# Some columns will dropped immediately as pre-processing.
drops = [
    'nces-id',
    'school-summary',
    'street',
    'fipscounty',
    'phone',
    'fax',
    'web-site',
    'overview-url',
    'rating-description',
    'distance',
]

# Grab data for Boston.
refresh = False
boston_nearby_schools_file = '../data/nearby_schools/boston.csv'
if refresh:
    boston_schools = get_nearby_schools(api_key,"42.3","-71.2","50")
    boston_df = pd.DataFrame.from_dict(boston_schools)
    boston_df.drop(columns=drops,inplace=True)
    boston_df.to_csv(boston_nearby_schools_file, )
else:
    boston_df = pd.read_csv(boston_nearby_schools_file)
    boston_df.set_index(keys=["universal-id"], drop=True, inplace=True)
    boston_df.drop(columns=["Unnamed: 0"], inplace=True)

# Grab data for Buffalo.
refresh = False
buffalo_nearby_schools_file = '../data/nearby_schools/buffalo.csv'
if refresh:
    buffalo_schools = get_nearby_schools(api_key,"42.9625","-78.7425","50")
    buffalo_df = pd.DataFrame.from_dict(buffalo_schools)
    buffalo_df.drop(columns=drops,inplace=True)
    buffalo_df.to_csv(buffalo_nearby_schools_file)
else:
    buffalo_df = pd.read_csv(buffalo_nearby_schools_file)
    buffalo_df.set_index(keys=["universal-id"], drop=True, inplace=True)
    buffalo_df.drop(columns=["Unnamed: 0"], inplace=True)

Process the `lat` and `lon` columns from the API output into tuples.

Then create two new columns:
- Distance to Downtown
- Distance to Work

In [4]:
# Form tuple to represent coordinates
boston_df['coordinates'] = list(zip(boston_df.lat,boston_df.lon))
#boston_df.drop(columns=['lat', 'lon'], inplace=True)

# Define coordinates of important places
downtown=(42.3674836866797, -71.07134540735377) # Science Museum
work=(42.47381059540949, -71.25414135292398) # Hartwell

# Create new columns to tabulate distance to these important places
boston_df['distance-to-downtown'] = boston_df['coordinates'].apply(func=get_distance,p2=downtown)
boston_df['distance-to-work'] = boston_df['coordinates'].apply(func=get_distance,p2=work)

We should definitely removal all schools that aren't in Massachusetts.

In [5]:
print(f'There are {len(boston_df)} schools from the original API results.')

# only allow from MA
boston_df = boston_df[boston_df['state'] == "MA"]
print(f'Allowing only schools from Massachusetts reduces the dataset to {len(boston_df)} schools.')

There are 1789 schools from the original API results.
Allowing only schools from Massachusetts reduces the dataset to 1375 schools.


How many unique district id's are there?

In [6]:
# get unique districts
districts = boston_df["district-id"].unique()
print(f'\nThere are {len(districts)} unique school districts.\n')


There are 230 unique school districts.



Which of these districts are close to both work and downtown boston?

In [7]:
# calculate distance to PoI using geo-center of districts
distances_to_downtown = {k: np.mean(list(v)) for k, v in boston_df.groupby('district-id')['distance-to-downtown']}
distances_to_work = {k: np.mean(list(v)) for k, v in boston_df.groupby('district-id')['distance-to-work']}

df_downtown = pd.DataFrame.from_dict(distances_to_downtown, orient='index')
df_work = pd.DataFrame.from_dict(distances_to_work, orient='index')

# merge these new columns
both_df = pd.merge(left=df_downtown, right=df_work, how='inner', left_index=True, right_index=True)
both_df.rename(columns={'0_x': "downtown", '0_y': "work"}, inplace=True)

both_df = both_df[both_df["downtown"] < 35.0]
both_df = both_df[both_df["work"] < 20.0]

print(f'\nThere are {len(both_df)} school districts within reasonable proximity to downtown and work.\n')

# filter out all schools which aren't in proximal districts
proximal_district_ids = list(both_df.index)
boston_df = boston_df[boston_df['district-id'].isin(proximal_district_ids)]

print(f'There are {len(boston_df)} schools within these proximal districts.\n')


There are 90 school districts within reasonable proximity to downtown and work.

There are 699 schools within these proximal districts.



Let's drop any districts that have an average rating below the school population mean.

In [8]:
# get the mean rating from the entire population of schools
mean_rating = boston_df['rating'].mean()
std_rating = boston_df['rating'].std()

print(f'\nOf the remaining {len(boston_df)} schools, the average rating is {mean_rating}.')

# compute the average rating for each district
ave_ratings = {k: np.mean(v) for k, v in boston_df.groupby(by='district-id')['rating']}

# keep only districts that are above the population mean
not_low_performing = [k for k, v in ave_ratings.items() if v > mean_rating]
boston_df = boston_df[boston_df['district-id'].isin(not_low_performing)]

districts = sorted(list(boston_df['district-name'].unique()))
print(f'\nThere are {len(districts)} districts remaining after pruning districts whose collective average is below the population mean rating.\n')
print(f'Which are, {districts}')


Of the remaining 699 schools, the average rating is 5.664546899841017.

There are 56 districts remaining after pruning districts whose collective average is below the population mean rating.

Which are, ['Acton-Boxborough School District', 'Andover School District', 'Arlington Public Schools', 'Ashland School District', 'Assabet Valley Regional Vocational Technical School District', 'Bedford School District', 'Belmont School District', 'Billerica School District', 'Boxford School District', 'Brookline School District', 'Burlington School District', 'Cambridge School District', 'Carlisle School District', 'Chelmsford School District', 'Concord School District', 'Concord-Carlisle School District', 'Dover School District', 'Dover-Sherborn School District', 'Dracut School District', 'Essex North Shore Agricultural and Technical School District', 'Groton-Dunstable School District', 'Harvard School District', 'Lexington School District', 'Lincoln-Sudbury School District', 'Littleton School 

In [9]:
boston_df.reset_index(inplace=True)
boston_df.set_index(['district-name','name'],inplace=True)
boston_df.sort_index(inplace=True)
boston_df.sample(5)

universal-id  \
district-name                name                                               
Quincy School District       Central Middle School                    2501385   
Natick School District       Brown                                    2501156   
Wakefield School District    Dolbeare Elementary School               2501667   
Southborough School District Albert S. Woodward Memorial School       2503218   
Wilmington School District   Wildwood                                 2501816   

                                                                 state-id  \
district-name                name                                           
Quincy School District       Central Middle School                2430315   
Natick School District       Brown                                1980010   
Wakefield School District    Dolbeare Elementary School           3050005   
Southborough School District Albert S. Woodward Memorial School   2760050   
Wilmington School District   Wildwood                             3420015   

                                                                   type  \
district-name                name                                         
Quincy School District       Central Middle School               public   
Natick School District       Brown                               public   
Wakefield School District    Dolbeare Elementary School          public   
Southborough School District Albert S. Woodward Memorial School  public   
Wilmington School District   Wildwood                            public   

                                                                level-codes  \
district-name                name                                             
Quincy School District       Central Middle School                        m   
Natick School District       Brown                                        e   
Wakefield School District    Dolbeare Elementary School                   e   
Southborough School District Albert S. Woodward Memorial School           e   
Wilmington School District   Wildwood                                   p,e   

                                                                      level  \
district-name                name                                             
Quincy School District       Central Middle School                    6,7,8   
Natick School District       Brown                               KG,1,2,3,4   
Wakefield School District    Dolbeare Elementary School          KG,1,2,3,4   
Southborough School District Albert S. Woodward Memorial School         2,3   
Wilmington School District   Wildwood                                 PK,KG   

                                                                         city  \
district-name                name                                               
Quincy School District       Central Middle School                     Quincy   
Natick School District       Brown                                     Natick   
Wakefield School District    Dolbeare Elementary School             Wakefield   
Southborough School District Albert S. Woodward Memorial School  Southborough   
Wilmington School District   Wildwood                              Wilmington   

                                                                state   zip  \
district-name                name                                             
Quincy School District       Central Middle School                 MA  2170   
Natick School District       Brown                                 MA  1760   
Wakefield School District    Dolbeare Elementary School            MA  1880   
Southborough School District Albert S. Woodward Memorial School    MA  1772   
Wilmington School District   Wildwood                              MA  1887   

                                                                           county  \
district-name                name                                                   
Quincy School District       Ce

In [10]:
#print(boston_df['level-codes'].unique()) 

In [11]:
#boston_df.loc["Quincy School District"]

In [12]:
from district_score import get_overall_rating

overall_df = get_overall_rating(boston_df)
overall_df = overall_df.set_index(keys='district-name', drop=True)
overall_df.sort_values(by='weighted_ave', ascending=False, inplace=True)
overall_df.reset_index(inplace=True)
overall_df.index += 1
#print(overall_df.to_markdown())

In [14]:
boston_schools = get_demographics(api_key,'2500919')

{'message': 'Too Many Requests'}
